# Auto-encoders

Até o momento, trabalhamos com a ideia de encontrar mapeamentos de textos para classes. Para isso, passamos por uma etapa que é encontrar uma representação intermediária para os textos. Agora, vamos tentar encontrar representações intermediárias à partir de dados não-rotulados, isto é, com a ideia de que vamos reduzir a dimensionalidade dos dados de entrada buscando minimizar ao máximo o erro de reconstituição.

In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder

from keras.layers import Input, Dense, Activation, TextVectorization, Reshape, RepeatVector, Conv1D, AveragePooling1D, UpSampling1D, Embedding, GlobalAveragePooling1D, LSTM
from keras.models import Model
import tensorflow as tf

import plotly.express as px

## Exercício 1
**Objetivo: usar um auto-encoder linear (PCA)**

1. Leia e interprete o código abaixo e explique o que está acontecendo.
1. O que está sendo plotado?
1. Por que esse plot não tem o formato de linha que vimos até agora? 

In [2]:
df = pd.read_csv('datasets/IMDB Dataset.csv')
reviews = df['review']
vocab_size = 1000
vectorize_layer = TextVectorization(output_mode='multi_hot', max_tokens=vocab_size, pad_to_max_tokens=True)
vectorize_layer.adapt(reviews)
X = vectorize_layer(reviews)

Metal device set to: Apple M1 Pro

systemMemory: 16.00 GB
maxCacheSize: 5.33 GB



2023-04-25 11:17:10.514218: W tensorflow/tsl/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz


In [3]:
def pca_autoencoder(vocab_size):
    input_layer = Input(shape=(vocab_size,))
    x = input_layer
    x_enc = Dense(2, name='encoder')(x)
    x = Dense(vocab_size, name='decoder')(x_enc)
    return Model(input_layer, x), Model(input_layer, x_enc)


pca, enc = pca_autoencoder(vocab_size)
print(pca.summary())
pca.compile(loss='mse')
history = pca.fit(X, X, epochs=5, verbose=1)

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 1000)]            0         
                                                                 
 encoder (Dense)             (None, 2)                 2002      
                                                                 
 decoder (Dense)             (None, 1000)              3000      
                                                                 
Total params: 5,002
Trainable params: 5,002
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/5
1563/1563 [==============================] - 12s 7ms/step - loss: 0.0610
Epoch 2/5
1563/1563 [==============================] - 12s 8ms/step - loss: 0.0597
Epoch 3/5
1563/1563 [==============================] - 11s 7ms/step - loss: 0.0594
Epoch 4/5
1563/1563 [==============================] - 11s 7ms/step -

In [188]:
X_enc = enc(X)
df['enc_x1'] = X_enc[:,0]
df['enc_x2'] = X_enc[:,1]

plt.figure()
fig = px.scatter(df, x="enc_x1", y="enc_x2", color="sentiment", title="Como os documentos se espalham?", width=600, height=600)
fig.show()

<Figure size 640x480 with 0 Axes>

# Exercício 2
**Objetivo: entender o autoencoder como uma sequência de um encoder e um decoder**

O código abaixo é equivalente ao código anterior que fizemos. Como funciona o "encoder"? Como funciona o "decoder"? Explique a função de cada um deles.

In [189]:
def encoder(vocab_size, target_size):
    input_layer = Input(shape=(vocab_size,))
    x = input_layer
    x = Dense(target_size, name='encoder')(x)
    return Model(input_layer, x)

def decoder(latent_size, target_size):
    input_layer = Input(shape=(latent_size,))
    x = input_layer
    x = Dense(target_size, name='decoder')(x)
    return Model(input_layer, x)

def autoencoder(encoder, decoder):
    in_shape = encoder.layers[0].input_shape[0]
    input_layer = Input(shape=in_shape)
    x = input_layer
    x = encoder(x)
    x = decoder(x)
    return Model(input_layer, x)

In [190]:
enc = encoder(vocab_size, 2)
#print(enc.layers[0].input_shape)
dec = decoder(2, vocab_size)
ae = autoencoder(enc, dec)

ae.compile(loss='mse')
#print(enc.get_layer('encoder').weights[0][0:5])
history = ae.fit(X, X, epochs=5, verbose=1)
#print(enc.get_layer('encoder').weights[0][0:5])

Epoch 1/5
1563/1563 [==============================] - 5s 3ms/step - loss: 0.0618
Epoch 2/5
1563/1563 [==============================] - 5s 3ms/step - loss: 0.0596
Epoch 3/5
1563/1563 [==============================] - 5s 3ms/step - loss: 0.0594
Epoch 4/5
1563/1563 [==============================] - 5s 3ms/step - loss: 0.0593
Epoch 5/5
1563/1563 [==============================] - 5s 3ms/step - loss: 0.0593


# Exercício 3
**Objetivo: entender autoencoders como mapeadores**

Podemos adicionar não-linearidades (ativações) tanto ao encoder quanto ao decoder. Com isso, podemos potencialmente aumentar a expressividade do nosso encoder e do decoder.

1. Verifique o erro de aproximação do autoencoder como está implementado.
1. Adicione camadas ao encoder e ao decoder de forma que o processo de redução de dimensão seja gradual, isto é, a queda de dimensão entre duas camadas seja mais suave que a atual. O que acontece com o modelo, com a representação, e com o erro de reconstituição?

In [250]:
def encoder(vocab_size, target_size):
    input_layer = Input(shape=(vocab_size,))
    x = input_layer
    x = Dense(target_size, activation='sigmoid')(x)
    return Model(input_layer, x)

def decoder(latent_size, target_size):
    input_layer = Input(shape=(latent_size,))
    x = input_layer
    x = Dense(target_size, activation='sigmoid')(x)
    return Model(input_layer, x)

def autoencoder(encoder, decoder):
    in_shape = encoder.layers[0].input_shape[0]
    input_layer = Input(shape=in_shape)
    x = input_layer
    x = encoder(x)
    x = decoder(x)
    return Model(input_layer, x)

enc = encoder(vocab_size, 20)
dec = decoder(20, vocab_size)
ae = autoencoder(enc, dec)
ae.compile(loss='mse')
history = ae.fit(X, X, epochs=15, verbose=1)


Epoch 1/15
1563/1563 [==============================] - 11s 6ms/step - loss: 0.0791
Epoch 2/15
1563/1563 [==============================] - 16s 10ms/step - loss: 0.0642
Epoch 3/15
1563/1563 [==============================] - 17s 11ms/step - loss: 0.0638
Epoch 4/15
1563/1563 [==============================] - 17s 11ms/step - loss: 0.0637
Epoch 5/15
1563/1563 [==============================] - 14s 9ms/step - loss: 0.0637
Epoch 6/15
1563/1563 [==============================] - 12s 8ms/step - loss: 0.0637
Epoch 7/15
1093/1563 [===================>..........] - ETA: 4s - loss: 0.0636

KeyboardInterrupt: 

In [251]:
X_enc = enc(X)
df['enc_x1'] = X_enc[:,0]
df['enc_x2'] = X_enc[:,1]


plt.figure()
fig = px.scatter(df, x="enc_x1", y="enc_x2", color="sentiment", title="Como os documentos se espalham?", width=600, height=600)
fig.show()

<Figure size 640x480 with 0 Axes>

# Exercício 4
**Objetivo: entender o auto-encoder auto-regressivo com LSTM**

O código abaixo mostra um auto-enconder auto-regressivo usando LSTM. 

1. Quais são as dimensões da entrada e da saída do encoder?
1. Quais são as dimensões da entrada e da saída do decoder?
1. O auto-encoder não trabalha mais com uma representação tipo bag-of-words, e sim com uma representação one-hot para cada uma das palavras do vocabulário. Qual é o consumo de memória dessa representação?
1. O que é possível visualizar no estado latente encontrado? 

In [252]:
def encoder(seq_len, latent_dim, vocab_size):
    input_layer = Input(shape=(seq_len, vocab_size))
    x = input_layer
    x, state_h, state_c = LSTM(latent_dim, return_state=True)(x)
    return Model(input_layer, [x, state_h, state_c])

def decoder(seq_len, latent_dim, vocab_size):
    input_x = Input(shape=(latent_dim))
    input_h = Input(shape=(latent_dim,))
    input_c = Input(shape=(latent_dim,))
    x = RepeatVector(seq_len)(input_x)
    x = LSTM(latent_dim, return_sequences=True)(x,initial_state=[input_h, input_c])
    x = Dense(vocab_size, activation='softmax')(x)
    return Model([input_x, input_h, input_c], x)

def autoencoder(encoder, decoder):
    in_shape = encoder.layers[0].input_shape[0][1:]
    print(in_shape)
    input_layer = Input(shape=in_shape)
    x = input_layer
    x = encoder(x)
    x = decoder(x)
    return Model(input_layer, x)

enc = encoder(200, 50, 1000)
enc.summary()
dec = decoder(200, 50, 1000)
dec.summary()
ae = autoencoder(enc, dec)
ae.compile(loss='categorical_crossentropy', optimizer='adam')
ae.summary()


Model: "model_253"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_345 (InputLayer)      [(None, 200, 1000)]       0         
                                                                 
 lstm_70 (LSTM)              [(None, 50),              210200    
                              (None, 50),                        
                              (None, 50)]                        
                                                                 
Total params: 210,200
Trainable params: 210,200
Non-trainable params: 0
_________________________________________________________________
Model: "model_254"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_346 (InputLayer)         [(None, 50)]         0           []                               

In [253]:
df = pd.read_csv('datasets/IMDB Dataset.csv').sample(1000)
reviews = df['review']
vocab_size = 1000
vectorize_layer = TextVectorization(max_tokens=vocab_size, output_sequence_length=200)
vectorize_layer.adapt(reviews)
X = vectorize_layer(reviews)
X = tf.one_hot(X, vocab_size)
print(X.shape)


(1000, 200, 1000)


In [254]:
history = ae.fit(X, X, epochs=20, verbose=1)

Epoch 1/20
32/32 [==============================] - 32s 654ms/step - loss: 6.2578
Epoch 2/20
32/32 [==============================] - 23s 722ms/step - loss: 4.5692
Epoch 3/20
32/32 [==============================] - 24s 746ms/step - loss: 4.2558
Epoch 4/20
32/32 [==============================] - 21s 662ms/step - loss: 4.2346
Epoch 5/20
32/32 [==============================] - 20s 632ms/step - loss: 4.2063
Epoch 6/20
32/32 [==============================] - 21s 651ms/step - loss: 4.1775
Epoch 7/20
32/32 [==============================] - 20s 624ms/step - loss: 4.1312
Epoch 8/20
32/32 [==============================] - 22s 673ms/step - loss: 4.0680
Epoch 9/20
32/32 [==============================] - 20s 611ms/step - loss: 4.0140
Epoch 10/20
32/32 [==============================] - 19s 585ms/step - loss: 3.9560
Epoch 11/20
32/32 [==============================] - 19s 579ms/step - loss: 3.9025
Epoch 12/20
32/32 [==============================] - 21s 657ms/step - loss: 3.8579
Epoch 13/20
3

In [196]:
X_enc, _, _ = enc(X)
df['enc_x1'] = X_enc[:,0]
df['enc_x2'] = X_enc[:,1]
plt.figure()
fig = px.scatter(df, x="enc_x1", y="enc_x2", color="sentiment", title="Como os documentos se espalham?", width=600, height=600)
fig.show()

<Figure size 640x480 with 0 Axes>

## Exercício 5
**Objetivo: verificar as ditorções causadas pelo autoencoder de sequências**

O código abaixo permite inserir textos e ler textos gerados pelo autoencoder. Que tipo de distorções você consegue verificar?

In [271]:
textos = df['review'][0:3]
X_ = vectorize_layer(textos)
X_ = tf.one_hot(X_, vocab_size)
X_transf = ae.predict(X_)
X_transf = X_transf.argmax(axis=-1)
X_texts = []
for i in range(X_transf.shape[0]):
    this_text = [vectorize_layer.get_vocabulary()[j] for j in X_transf[i,:]]
    X_texts.append(this_text)
    print(this_text)

1/1 [==============================] - 0s 276ms/step
['[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '

## Exercício 6
**Objetivo: usar um encoder numa downstream task de classificação**

Observe o código abaixo.

1. Como o encoder já treinado é usado?
1. Como "avisamos" ao keras para ajustar ou não os pesos do encoder de acordo com os rótulos da tarefa de classificação?
1. Como o espaço latente do encoder se modifica ao fazermos a tarefa de classificação?

In [272]:
df = pd.read_csv('datasets/IMDB Dataset.csv').sample(1000)
ohe = OneHotEncoder()
y_ohe = ohe.fit_transform(df['sentiment'].to_numpy().reshape((-1,1))).todense()
X_train, X_test, y_train, y_test = train_test_split(df['review'], y_ohe)

reviews = df['review']
vocab_size = 1000
vectorize_layer = TextVectorization(max_tokens=vocab_size, output_sequence_length=200)
vectorize_layer.adapt(X_train)
X_train = vectorize_layer(X_train)
X_train = tf.one_hot(X_train, vocab_size)
X_test = vectorize_layer(X_test)
X_test = tf.one_hot(X_test, vocab_size)

In [273]:
def transfer_classifier(encoder):
    in_shape = encoder.layers[0].input_shape[0][1:]
    input_layer = Input(shape=in_shape)
    x = input_layer
    encoder.trainable=False
    x, _, _ = encoder(x)
    x = Dense(2, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)

clf = transfer_classifier(encoder=enc)
print(clf.summary())
clf.compile(loss='categorical_crossentropy', metrics=['accuracy'])
history = clf.fit(X_train, y_train, epochs=20, verbose=1, validation_split=0.1)
clf.evaluate(X_test, y_test)

Model: "model_256"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_350 (InputLayer)      [(None, 200, 1000)]       0         
                                                                 
 model_253 (Functional)      [(None, 50),              210200    
                              (None, 50),                        
                              (None, 50)]                        
                                                                 
 classificador (Dense)       (None, 2)                 102       
                                                                 
 activation_94 (Activation)  (None, 2)                 0         
                                                                 
Total params: 210,302
Trainable params: 102
Non-trainable params: 210,200
_________________________________________________________________
None
Epoch 1/20
22/22 [==========================

[0.7143243551254272, 0.46399998664855957]

In [199]:
def transfer_classifier(encoder):
    in_shape = encoder.layers[0].input_shape[0][1:]
    input_layer = Input(shape=in_shape)
    x = input_layer
    encoder.trainable=True
    x, _, _ = encoder(x)
    x = Dense(2, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)

clf = transfer_classifier(encoder=enc)
print(clf.summary())
clf.compile(loss='categorical_crossentropy', metrics=['accuracy'])
history = clf.fit(X_train, y_train, epochs=20, verbose=1, validation_split=0.1)
clf.evaluate(X_test, y_test)

Model: "model_148"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_231 (InputLayer)      [(None, 200, 1000)]       0         
                                                                 
 model_144 (Functional)      [(None, 5),               20120     
                              (None, 5),                         
                              (None, 5)]                         
                                                                 
 classificador (Dense)       (None, 2)                 12        
                                                                 
 activation_6 (Activation)   (None, 2)                 0         
                                                                 
Total params: 20,132
Trainable params: 20,132
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/20
22/22 [==============================

[0.7014766931533813, 0.492000013589859]

In [274]:
X_enc, _, _ = enc(X_test)
# df['enc_x1'] = X_enc[:,0]
# df['enc_x2'] = X_enc[:,1]
tags = ohe.inverse_transform(np.asarray(y_test)).reshape( (-1,))
plt.figure()
fig = px.scatter(x=X_enc[:,0], y=X_enc[:,1], color=tags, title="Como os documentos se espalham?", width=600, height=600)
fig.show()

<Figure size 640x480 with 0 Axes>

## Exercício 7
**Objetivo: analisar o pré-treinamento de um encoder convolucional**

O código abaixo faz o mesmo que foi feito com a LSTM, mas agora com uma CNN.

1. Como os resultados obtidos se compararm aos da LSTM?
1. Como os resultados obtidos se comparam aos que foram obtidos na aula anterior?
1. Por que existem essas diferenças?
1. Quais seriam passos relevantes para mitigar esses problemas futuramente?

In [275]:
def convolve_and_downsample(input_n_samples, input_embedding_size, n_filters, kernel_size=3, **kwargs):
    input_layer = Input(shape=(input_n_samples,input_embedding_size))
    x = input_layer
    x = Conv1D( filters=n_filters,
                kernel_size=kernel_size,
                padding='same',
                use_bias=False,
                )(x)
    x = AveragePooling1D(pool_size=2)(x)
    x = Activation('elu')(x)
    return Model(input_layer, x, **kwargs)

def upsample_and_convolve(input_n_samples, input_embedding_size, n_filters, kernel_size=3, **kwargs):
    input_layer = Input(shape=(input_n_samples,input_embedding_size))
    x = input_layer
    x = UpSampling1D(size=2)(x)
    x = Conv1D( filters=n_filters,
                kernel_size=kernel_size,
                padding='same',
                use_bias=False,
                )(x)

    x = Activation('elu')(x)
    return Model(input_layer, x, **kwargs)


In [276]:
def cnn_encoder(seq_len, vocab_size=vocab_size, number_of_ngrams=64, n_gram_size=3):
    input_layer = Input(shape=(seq_len, vocab_size))
    x = input_layer
    x = convolve_and_downsample(128, vocab_size, number_of_ngrams, n_gram_size)(x)
    x = convolve_and_downsample(64, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = convolve_and_downsample(32, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = convolve_and_downsample(16, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = convolve_and_downsample(8, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = convolve_and_downsample(4, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = convolve_and_downsample(2, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    return Model(input_layer, x)

def cnn_decoder(seq_len, vocab_size=vocab_size, number_of_ngrams=64, n_gram_size=3):
    input_layer = Input(shape=(1, number_of_ngrams))
    x = input_layer
    x = upsample_and_convolve(1, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = upsample_and_convolve(2, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = upsample_and_convolve(4, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = upsample_and_convolve(8, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = upsample_and_convolve(16, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = upsample_and_convolve(32, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = upsample_and_convolve(64, number_of_ngrams, number_of_ngrams, n_gram_size)(x)
    x = Dense(vocab_size, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)


enc = cnn_encoder(128, 1000)
enc.summary()
dec = cnn_decoder(128, 1000)
dec.summary()
ae = autoencoder(enc, dec)
ae.compile(loss='categorical_crossentropy', optimizer='adam')
ae.summary()

Model: "model_264"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_351 (InputLayer)      [(None, 128, 1000)]       0         
                                                                 
 model_257 (Functional)      (None, 64, 64)            192000    
                                                                 
 model_258 (Functional)      (None, 32, 64)            12288     
                                                                 
 model_259 (Functional)      (None, 16, 64)            12288     
                                                                 
 model_260 (Functional)      (None, 8, 64)             12288     
                                                                 
 model_261 (Functional)      (None, 4, 64)             12288     
                                                                 
 model_262 (Functional)      (None, 2, 64)             12

In [277]:
df = pd.read_csv('datasets/IMDB Dataset.csv').sample(1000)
reviews = df['review']
vocab_size = 1000
vectorize_layer = TextVectorization(max_tokens=vocab_size, output_sequence_length=128)
vectorize_layer.adapt(reviews)
X = vectorize_layer(reviews)
X = tf.one_hot(X, vocab_size)
print(X.shape)

(1000, 128, 1000)


In [278]:
history = ae.fit(X, X, epochs=20, verbose=1)

Epoch 1/20
32/32 [==============================] - 12s 175ms/step - loss: 5.3494
Epoch 2/20
32/32 [==============================] - 5s 164ms/step - loss: 4.4836
Epoch 3/20
32/32 [==============================] - 5s 148ms/step - loss: 4.4247
Epoch 4/20
32/32 [==============================] - 5s 148ms/step - loss: 4.4066
Epoch 5/20
32/32 [==============================] - 5s 153ms/step - loss: 4.4028
Epoch 6/20
32/32 [==============================] - 5s 149ms/step - loss: 4.3922
Epoch 7/20
32/32 [==============================] - 5s 147ms/step - loss: 4.3882
Epoch 8/20
32/32 [==============================] - 5s 153ms/step - loss: 4.3726
Epoch 9/20
32/32 [==============================] - 5s 148ms/step - loss: 4.3629
Epoch 10/20
32/32 [==============================] - 5s 150ms/step - loss: 4.3518
Epoch 11/20
32/32 [==============================] - 5s 152ms/step - loss: 4.3420
Epoch 12/20
32/32 [==============================] - 5s 147ms/step - loss: 4.3348
Epoch 13/20
32/32 [=====

In [279]:
df = pd.read_csv('datasets/IMDB Dataset.csv').sample(1000)
ohe = OneHotEncoder()
y_ohe = ohe.fit_transform(df['sentiment'].to_numpy().reshape((-1,1))).todense()
X_train, X_test, y_train, y_test = train_test_split(df['review'], y_ohe)

reviews = df['review']
vocab_size = 1000
vectorize_layer = TextVectorization(max_tokens=vocab_size, output_sequence_length=128)
vectorize_layer.adapt(X_train)
X_train = vectorize_layer(X_train)
X_train = tf.one_hot(X_train, vocab_size)
X_test = vectorize_layer(X_test)
X_test = tf.one_hot(X_test, vocab_size)

In [282]:
def transfer_classifier(encoder):
    in_shape = encoder.layers[0].input_shape[0][1:]
    input_layer = Input(shape=in_shape)
    x = input_layer
    encoder.trainable=False
    x = encoder(x)
    x = Reshape( (64,))(x)
    x = Dense(2, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)

clf = transfer_classifier(encoder=enc)
print(clf.summary())
clf.compile(loss='categorical_crossentropy', metrics=['accuracy'])
history = clf.fit(X_train, y_train, epochs=20, verbose=1, validation_split=0.1)
clf.evaluate(X_test, y_test)

Model: "model_274"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_370 (InputLayer)      [(None, 128, 1000)]       0         
                                                                 
 model_264 (Functional)      (None, 1, 64)             265728    
                                                                 
 reshape_5 (Reshape)         (None, 64)                0         
                                                                 
 classificador (Dense)       (None, 2)                 130       
                                                                 
 activation_110 (Activation)  (None, 2)                0         
                                                                 
Total params: 265,858
Trainable params: 130
Non-trainable params: 265,728
_________________________________________________________________
None
Epoch 1/20
22/22 [==========================

[0.7035152316093445, 0.5360000133514404]

In [283]:
textos = df['review'][0:3]
X_ = vectorize_layer(textos)
X_ = tf.one_hot(X_, vocab_size)
X_transf = ae.predict(X_)
X_transf = X_transf.argmax(axis=-1)
X_texts = []
for i in range(X_transf.shape[0]):
    this_text = [vectorize_layer.get_vocabulary()[j] for j in X_transf[i,:]]
    X_texts.append(this_text)
    print(this_text)

1/1 [==============================] - 1s 627ms/step
['this', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[

In [285]:
def transfer_classifier(encoder):
    in_shape = encoder.layers[0].input_shape[0][1:]
    input_layer = Input(shape=in_shape)
    x = input_layer
    encoder.trainable=True
    x = encoder(x)
    x = Reshape( (64,))(x)
    x = Dense(2, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)

clf = transfer_classifier(encoder=enc)
print(clf.summary())
clf.compile(loss='categorical_crossentropy', metrics=['accuracy'])
history = clf.fit(X_train, y_train, epochs=20, verbose=1, validation_split=0.1)
clf.evaluate(X_test, y_test)

Model: "model_275"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_372 (InputLayer)      [(None, 128, 1000)]       0         
                                                                 
 model_264 (Functional)      (None, 1, 64)             265728    
                                                                 
 reshape_7 (Reshape)         (None, 64)                0         
                                                                 
 classificador (Dense)       (None, 2)                 130       
                                                                 
 activation_111 (Activation)  (None, 2)                0         
                                                                 
Total params: 265,858
Trainable params: 265,858
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/20
22/22 [============================

[1.9857429265975952, 0.7360000014305115]

In [287]:
textos = df['review'][0:3]
X_ = vectorize_layer(textos)
X_ = tf.one_hot(X_, vocab_size)
X_transf = ae.predict(X_)
X_transf = X_transf.argmax(axis=-1)
X_texts = []



for i in range(X_transf.shape[0]):
    this_text = [vectorize_layer.get_vocabulary()[j] for j in X_transf[i,:]]
    X_texts.append(this_text)
    print(this_text)

1/1 [==============================] - 0s 60ms/step
['[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[UNK]', '[